# CAPSTONE PROJECT

#### The idea of this project is to provide the best location for a restaurant based on external sources of data. What I will try during this notebook is to show different sources of data to identify the best location.

#### DATASET USED
##### 1.- Foursquare info from previous week 
##### 2.- Neiborhoud boundaries from (https://open.toronto.ca/dataset/neighbourhoods/)
##### 3.- Business Improvement areas (https://open.toronto.ca/dataset/business-improvement-areas/)


During this notebook I will try to link the situation of the main food related placed in the city of toronto with the biggest business development area. This will lead us to find which is the % of restaurantes in each area and the proportion compared to the rest.
Based on this if we want to place a restaurant it should be done in the best business area with the lowest restaurant rate

#### METHODOLOGY
I provide an study where I evaluate the realtionship between the number of elements in each area compared with the number of food related ones. Lowest ratio is the indicator to place the restaurant

In [1]:
import pandas as pd
import numpy as np
import matplotlib.cm as cm
from scipy.spatial import distance_matrix 
import matplotlib.colors as colors
import folium # plotting library
from sklearn.cluster import KMeans 
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values
from math import cos, asin, sqrt
%matplotlib inline 

#### READ Datasets


In [2]:
# Foursquare data:
df_square=pd.read_csv('Toronto_data.csv')
df_square.head()




Unnamed: 0    Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0           0           Rouge              43.806686              -79.194353   
1           1         Malvern              43.806686              -79.194353   
2           2  Highland Creek              43.784535              -79.160497   
3           3  Highland Creek              43.784535              -79.160497   
4           4      Rouge Hill              43.784535              -79.160497   

                       Venue  Venue Latitude  Venue Longitude  \
0                    Wendy's       43.807448       -79.199056   
1                    Wendy's       43.807448       -79.199056   
2      Royal Canadian Legion       43.782533       -79.163085   
3  Affordable Toronto Movers       43.787919       -79.162977   
4      Royal Canadian Legion       43.782533       -79.163085   

         Venue Category  
0  Fast Food Restaurant  
1  Fast Food Restaurant  
2                   Bar  
3         Moving Target  
4                   Bar

In [3]:
df_areas=pd.read_csv('Business Improvement Areas Data.csv')
df_areas.head()


_id  AREA_ID       DATE_EFFECTIVE  AREA_ATTR_ID  PARENT_AREA_ID  \
0  739  2478937  2019-05-28T21:47:59      26004921             NaN   
1  740  2478936  2019-05-28T21:47:59      26004920             NaN   
2  741  2478935  2019-05-28T21:47:59      26004919             NaN   
3  742  2478934  2019-05-28T21:47:59      26004918             NaN   
4  743  2478933  2019-05-28T21:47:59      26004917             NaN   

  AREA_SHORT_CODE AREA_LONG_CODE          AREA_NAME          AREA_DESC  \
0          020-01         020-01       Little Italy       Little Italy   
1          042-01         042-01    Liberty Village    Liberty Village   
2          093-01         093-01        Leslieville        Leslieville   
3          033-00         033-00       Kennedy Road       Kennedy Road   
4          002-00         002-00  Lakeshore Village  Lakeshore Village   

            X            Y  LONGITUDE   LATITUDE  OBJECTID   Shape__Area  \
0  311705.037  4835053.901 -79.414394  43.655397  17536177  2.323416e+05   
1  311152.727  4833083.985 -79.421265  43.637670  17536193  7.972921e+05   
2  318224.026  4835848.463 -79.333555  43.662460  17536209  3.513029e+05   
3  322480.719  4847294.113 -79.280401  43.765395  17536225  1.830952e+06   
4  304525.971  4829026.074 -79.503394  43.601170  17536241  1.719640e+05   

   Shape__Length                                           geometry  
0    3917.542802  {u'type': u'MultiPolygon', u'coordinates': [((...  
1    4400.913504  {u'type': u'MultiPolygon', u'coordinates': [((...  
2    6457.749078  {u'type': u'MultiPolygon', u'coordinates': [((...  
3   13312.406690  {u'type': u'MultiPolygon', u'coordinates': [((...  
4    3336.398221  {u'type': u'MultiPolygon', u'coordinates': [((...

In the code below we will assign the closest business area based on distance to the center of the area. This way we can calculate the total number of places by AREA, which will give us a size of it.

In [4]:
def distance(lat1, lon1, lat2, lon2):
    p = 0.017453292519943295
    a = 0.5 - cos((lat2-lat1)*p)/2 + cos(lat1*p)*cos(lat2*p) * (1-cos((lon2-lon1)*p)) / 2
    return 12742 * asin(sqrt(a))

def closest(data, v):
    return min(data, key=lambda p: distance(v['LATITUDE'],v['LONGITUDE'],p['LATITUDE'],p['LONGITUDE']))['AREA_NAME']






def find_area():
    tempData = []
    for index, row in df_areas.iterrows():
        tempDict = {}
        tempDict['LATITUDE']=row['LATITUDE']
        tempDict['LONGITUDE']=row['LONGITUDE']
        tempDict['AREA_NAME']=row['AREA_NAME']
        tempData.append(tempDict)
    return_value=[]
    for index, row in df_square.iterrows():
        temp_results = {}
        tempRow = {'LATITUDE': row['Venue Latitude'], 'LONGITUDE': row['Venue Longitude']}
        temp_results['AREA']=closest(tempData,tempRow)
        temp_results['Venue Category']=row['Venue Category']
        temp_results['Venue Latitude']=row['Venue Latitude']
        temp_results['Venue Longitude']=row['Venue Longitude']
        return_value.append(temp_results)
    return return_value
        
df_square['AREA']=""
df_temp_rest=find_area()


df = pd.DataFrame(df_temp_rest, columns =['AREA', 'Venue Category' ,'Venue Latitude','Venue Longitude' ]) 

data_grouped=df.groupby("AREA")["AREA"].count()

df_n = pd.DataFrame(data_grouped, columns=['AREA']) 

df_n.rename(columns={'AREA':'Total'},inplace=True)

df_population=df_n.sort_values(by=['Total'],ascending=False)



#### First let's find out where are the actual restaurants placed

In [5]:
df.loc[df['Venue Category'].str.contains("Restaurant"), 'food_related'] = True 
df.loc[df['Venue Category'].str.contains("Gastropub"), 'food_related'] = True 
#df_square.loc[df_square['Venue Category'].str.contains("Bar"), 'food_related'] = True 


df_area_food=df[df['food_related'] == True]
len(df_area_food)

df_area_grouped=df_area_food.groupby("AREA")["AREA"].count()
df_area_grouped = pd.DataFrame(df_area_grouped, columns =['AREA']) 
df_area_grouped.rename(columns={'AREA':'Total'},inplace=True)

df_restaurants=df_area_grouped.sort_values(by=['Total'],ascending=False)



Let's find out which is the best business area based on the propotion of restaurants

In [6]:
# Number of Items
df_population

# Number of Restaurants
df_restaurants

df_test=df_population.join(df_restaurants, lsuffix='_caller', rsuffix='_other')

df_test['Ratio']=(df_test['Total_other']*100)/df_test['Total_caller']

df_test=df_test.reset_index()

df_test.head()



AREA  Total_caller  Total_other      Ratio
0              Financial District           976        262.0  26.844262
1                  Downtown Yonge           305         65.0  21.311475
2  Toronto Entertainment District           249         38.0  15.261044
3                    Kennedy Road           204         59.0  28.921569
4               Kensington Market           199         60.0  30.150754

In [7]:
address = 'Toronto'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Toronto are {}, {}.'.format(latitude, longitude))
map_toronto = folium.Map(location=[latitude, longitude], zoom_start=10)


The geograpical coordinate of Toronto are 43.653963, -79.387207.


In [8]:
for lat, lng, venue_type in zip(df['Venue Latitude'], df['Venue Longitude'], df['Venue Category']):
    label = '{}'.format(venue_type)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_toronto)  

for lat, lng, area_name in zip(df_areas['LATITUDE'], df_areas['LONGITUDE'], df_areas['AREA_NAME']):
    label = '{}'.format(area_name)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='red',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_toronto)  
    
map_toronto

In [12]:
# Print the investment area with less ratio restaurant / rest

df_ratio=df_test.sort_values(by=['Ratio'],ascending=True)
df_ratio

AREA  Total_caller  Total_other     Ratio
23  Village of Islington            57          3.0  5.263158
45          Pape Village            17          1.0  5.882353
37        Weston Village            32          2.0  6.250000
40      MarkeTO District            29          2.0  6.896552
30     Queen Street West            42          3.0  7.142857
..                   ...           ...          ...       ...
68     Bloor By The Park             2          NaN       NaN
69         Midtown Yonge             2          NaN       NaN
70     Hillcrest Village             1          NaN       NaN
71      Wychwood Heights             1          NaN       NaN
72       Oakwood Village             1          NaN       NaN

[73 rows x 4 columns]

#### RESULTS
In this section we can see that Village of Islington is the best area for a Restaurant


In [22]:
df_winner = df_areas[df_areas['AREA_NAME'] == 'Village of Islington' ]
df_winner


_id  AREA_ID       DATE_EFFECTIVE  AREA_ATTR_ID  PARENT_AREA_ID  \
59  798  2478878  2019-05-28T21:47:59      26004862             NaN   

   AREA_SHORT_CODE AREA_LONG_CODE             AREA_NAME             AREA_DESC  \
59          026-01         026-01  Village of Islington  Village of Islington   

            X            Y  LONGITUDE   LATITUDE  OBJECTID    Shape__Area  \
59  302251.36  4833791.918 -79.531591  43.644065  17537121  661985.925781   

    Shape__Length                                           geometry  
59    7141.265616  {u'type': u'MultiPolygon', u'coordinates': [((...

In [23]:
map_winner = folium.Map(location=[df_winner.iloc[0]['LATITUDE'], df_winner.iloc[0]['LONGITUDE']], zoom_start=20)
label = '{}'.format(df_winner.iloc[0]['AREA_NAME'])
label = folium.Popup(label, parse_html=True)
folium.CircleMarker(
    [df_winner.iloc[0]['LATITUDE'], df_winner.iloc[0]['LONGITUDE']],
    radius=5,
    popup=label,
    color='red',
    fill=True,
    fill_color='#3186cc',
    fill_opacity=0.7,
    parse_html=False).add_to(map_winner)  
map_winner

#### CONCLUSION

As a summary of this exercise we can evaluate which are the areas where Toronto has been investing in business development.
This situation generates a great ecosystem to generate business development in the area, in our analysis we have established
the ratio between different business that are in the area.
Based on both ideas, we can summarize that if an area is growing fast and the restaurant ratio is smaller than the rest we can
ensure that this area will be a good investment point for a food place.